In [1]:
import nltk
import json
import math
from nltk.util import pr
import numpy as np  
import pandas as pd
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.cluster import KMeans
from sklearn import svm
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer

from pattern3.en import singularize
import re
Size = 26709


In [2]:
#Classification problem , either sarcastic or not sarcastic ,2 class problem
alpha = ''
Raw_Data = dict()
X_headline =[]
Y_Sarcastic=[]
i=0


In [3]:
stop_word = []
with open("Stopword-List.txt",'r') as stop:
    for line in stop:
        temp = line.strip()
        stop_word.append(temp)

In [4]:
# #Read data in X and Y labels ,headline and sarcacism score.
# #and tokenize
# #Tokenize
# Tokens = []
# count = 0
# for lines in open('Sarcasm_Headlines_Dataset.json','r'):
#     Raw_Data[i]=json.loads(lines)
#     X_headline.append(Raw_Data[i]["headline"])
#     Y_Sarcastic.append(Raw_Data[i]["is_sarcastic"])
    
#     #tokenize here
#     for word in X_headline[i]:
#         if(word == ' '):
#             count += 1
#             Tokens.append(alpha)
#             alpha = ''
#         else:
#             alpha = alpha + word
    
#     i=i+1
def cleaner(uncleaned):
    porter = PorterStemmer()
    lemma = WordNetLemmatizer()
    uncleaned = uncleaned.lower()
    uncleaned = uncleaned.strip()
    uncleaned = uncleaned.translate({ord(i): None for i in '!\\@#-_:$%^&*();.,?/1”2’3“4‘567890\'\"'})
    for i in uncleaned:
        t = ord(i)
        if t < 97 or t>122:
            uncleaned = uncleaned.replace(i, "")
    uncleaned = porter.stem(uncleaned)
    uncleaned = lemma.lemmatize(uncleaned, pos='v')
    # uncleaned = singularize(uncleaned)
    # uncleaned = re.sub(r'ly$', r'', uncleaned)
    # uncleaned = re.sub(r'ed$', r'', uncleaned)
    # uncleaned = re.sub(r'ing$', r'', uncleaned)
    # uncleaned = re.sub(r'nes$', r'', uncleaned)
    return uncleaned



In [6]:
#Read data in X and Y labels ,headline and sarcacism score.
#and tokenize
#Tokenize
from nltk.tokenize import word_tokenize
Tokens = []
count = 0
lexicon = {}
for lines in open('Sarcasm_Headlines_Dataset.json','r'):
    Raw_Data[i]=json.loads(lines)
    X_headline.append(Raw_Data[i]["headline"])
    Y_Sarcastic.append(Raw_Data[i]["is_sarcastic"])
    
    #tokenize here
    words = word_tokenize(X_headline[i])
    curr = str(i)
    for word in words:
        if len(word) > 2:
            if word in stop_word:
                continue
            word = cleaner(word)
            Tokens.append(word)

            if word in lexicon:
                if curr in lexicon[word]:
                    lexicon[word][i] += 1
                else:
                    lexicon[word][i] = 1
            else:
                lexicon[word] = {}
                if curr in lexicon[word]:
                    lexicon[word][i] += 1
                else:
                    lexicon[word][i] = 1
    i=i+1
    # print(word)
    # for word in X_headline[i]:
    #     if(word == ' '):
    #         count += 1
    #         Tokens.append(alpha)
    #         alpha = ''
    #     else:
    #         alpha = alpha + word
    
    

    



In [7]:
#Tokenize
# Tokens = []
# count = 0
# for y in range(len(X_headline)):
#     for word in X_headline[y]:
#         if(word == ' '):
#             count += 1
#             Tokens.append(alpha)
#             alpha = ''
#         else:
#             alpha = alpha + word
# print(Tokens)
print("The word count is: "+str(len(Tokens)))
print("Number of docs are: " + str(i))
# print(lexicon)
print("dictionary size is",len(lexicon))
# print(type(Raw_Data))

The word count is: 211132
Number of docs are: 26709
dictionary size is 18769


In [8]:
def make_idf(lexicon):
    idf = dict()
    N = Size
    for term,docs in lexicon.items():
        df = len(docs)
        temp = math.log(N / df)
        idf[term] = temp
    return idf

In [9]:
# def init_tf_idf_lexicon(lexicon):
#     tf_idf = dict()
#     for keys,values in lexicon.items():
#         tf_idf[keys] = {}
#         for leg in range(0,Size+1):
#             tf_idf[keys][leg] = float(0)
#     return tf_idf

def tf_idf_lexicon(lexicon,idf):
    tf_idf = {}
    for term,docs in lexicon.items():
        tf_idf[term] = {}
        for docNo,tf in docs.items():
            tf_idf[term][docNo] = tf * idf[term]

    return tf_idf

In [10]:
idf = make_idf(lexicon)
# print(idf)

# print(tf_idf)

In [11]:
tf_idf = tf_idf_lexicon(lexicon,idf)

In [12]:
print(tf_idf)

{'former': {0: 5.5387955160842575, 226: 5.5387955160842575, 488: 5.5387955160842575, 2681: 5.5387955160842575, 2800: 5.5387955160842575, 2935: 5.5387955160842575, 3200: 5.5387955160842575, 3280: 5.5387955160842575, 3511: 5.5387955160842575, 3547: 5.5387955160842575, 3647: 5.5387955160842575, 3960: 5.5387955160842575, 3987: 5.5387955160842575, 4004: 5.5387955160842575, 4607: 5.5387955160842575, 4789: 5.5387955160842575, 4929: 5.5387955160842575, 5573: 5.5387955160842575, 6235: 5.5387955160842575, 6658: 5.5387955160842575, 7066: 5.5387955160842575, 7293: 5.5387955160842575, 7869: 5.5387955160842575, 8402: 5.5387955160842575, 8428: 5.5387955160842575, 8803: 5.5387955160842575, 8996: 5.5387955160842575, 9409: 5.5387955160842575, 9672: 5.5387955160842575, 9726: 5.5387955160842575, 9824: 5.5387955160842575, 9877: 5.5387955160842575, 9904: 5.5387955160842575, 10580: 5.5387955160842575, 10605: 5.5387955160842575, 11002: 5.5387955160842575, 11140: 5.5387955160842575, 11142: 5.5387955160842575, 